In [8]:
from trainer.env import make_env
from trade_tester.tester_base_class import render_candles
from trade_utils.data import get_raw_klines
from trade_utils.vizualize import render_lines
import pandas as pd
import numpy as np
import xarray as xr
from keras.models import Sequential, Model
from keras import layers
from keras.callbacks import EarlyStopping
import tensorflow as tf
from metrics import f1_metric
import os
from help_functions import CustomDataGenerator
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from datetime import datetime

In [13]:
def log_diff(series: pd.Series):
    log_diff_values = np.insert(np.log(series.values[1:]) - np.log(series.values[:-1]), 0 , np.nan)
    
    # Находим минимальное и максимальное значения, исключая бесконечности
    min_val = np.min(log_diff_values[np.logical_and(~np.isnan(log_diff_values), ~np.isinf(log_diff_values))])
    max_val = np.max(log_diff_values[np.logical_and(~np.isnan(log_diff_values), ~np.isinf(log_diff_values))])
    
    # Заменяем бесконечности на минимальное и максимальное значения
    log_diff_values[log_diff_values == -np.inf] = min_val
    log_diff_values[log_diff_values == np.inf] = max_val

    return log_diff_values

def rel_diff(series: pd.Series):
    diff = series.diff()
    return diff.iloc[1:] / series.iloc[:-1]

def remove_outliers(df, cols):
    for col in cols:
        mean = df[col].mean()
        std = df[col].std()
        lower_bound = mean - 10*std
        upper_bound = mean + 10*std
        df[col] = np.where(df[col] < lower_bound, lower_bound, df[col])
        df[col] = np.where(df[col] > upper_bound, upper_bound, df[col])
    return df

# def remove_outliers(df, cols):
#     for col in cols:
#         Q1 = df[col].quantile(0.0001)
#         Q3 = df[col].quantile(0.9999)
#         df[col] = np.where(df[col] < Q1, Q1, df[col])
#         df[col] = np.where(df[col] > Q3, Q3, df[col])
#     return df

def split_data(data, split_percent):
    split_index = int(len(data) * split_percent)
    return data[:split_index].copy(), data[split_index:].copy()

In [14]:
indicators_kwargs = dict(
    bb=dict(render=True, color='yellow'),
    rsi=dict(),
    stochastic=dict(),
    obv={},
    atr={},
)
klines, indicators = get_raw_klines(symbol='BTCUSDT', tf='15m', preprocessing_kwargs=indicators_kwargs)

klines['close_log_diff'] = log_diff(klines['close'])
klines['high_log_diff'] = log_diff(klines['high'])
klines['low_log_diff'] = log_diff(klines['low'])
klines['bb_lower_log_diff'] = log_diff(klines['bb_lower'])
klines['bb_upper_log_diff'] = log_diff(klines['bb_upper'])
klines['bb_middle_log_diff'] = log_diff(klines['bb_middle'])
klines['volume_log_diff'] = log_diff(klines['volume'])
klines['trades_log_diff'] = log_diff(klines['trades'])
klines['obv_log_diff'] = log_diff(klines['obv'])
klines['atr_log_diff'] = log_diff(klines['atr'])

klines['buy'] = 0
klines['sell'] = 0
klines = klines.dropna().reset_index(drop=True)

for i, row in klines.iterrows():
    if row['close'] <= row['bb_lower']:
        mask = (klines['open_time'] > row['open_time']) & (klines['close'] >= klines['bb_middle'])
        close_kline = klines[mask].iloc[0]
        if close_kline['close'] > row['close']:
            klines.loc[i, 'buy'] = 1

/tmp/ipykernel_728509/2012686479.py:2: RuntimeWarning:

divide by zero encountered in log

/tmp/ipykernel_728509/2012686479.py:2: RuntimeWarning:

invalid value encountered in subtract

/tmp/ipykernel_728509/2012686479.py:2: RuntimeWarning:

divide by zero encountered in log

/tmp/ipykernel_728509/2012686479.py:2: RuntimeWarning:

invalid value encountered in subtract

/tmp/ipykernel_728509/2012686479.py:2: RuntimeWarning:

divide by zero encountered in log



In [12]:
render_lines(klines['rsi'])

In [ ]:
features = [
    'bb_lower_log_diff',
    'bb_upper_log_diff',
    'bb_middle_log_diff',
    'trades_log_diff',
    'volume_log_diff',
    'rsi',
]
util_cols = ['bb_lower', 'close', 'buy', 'open_time']
data = klines[[*features, *util_cols]]

In [ ]:
train, test = split_data(data, 0.8)

cols_for_removing_outliers = [
    'close_log_diff',
    'high_log_diff',
    'low_log_diff',
    'bb_lower_log_diff',
    'bb_upper_log_diff',
    'bb_middle_log_diff',
    'trades_log_diff',
    'volume_log_diff',
]
train = remove_outliers(train, cols=cols_for_removing_outliers)

In [ ]:
def make_observation_window(data, window_size:int):
    X, y, time = [], [], []
    for i in range(window_size, len(data)):
        if data.iloc[i]['close'] < data.iloc[i]['bb_lower']:
            X.append(data.iloc[i - window_size:i].drop(['bb_lower', 'close', 'buy', 'open_time'], axis=1))
            y.append(data.iloc[i]['buy'])
            time.append(data.iloc[i]['open_time'])
    da = xr.DataArray(np.array(X), dims=['time', 'y', 'z'], coords={'time': np.array(time)})
    return da, np.array(y)

X_train, y_train = make_observation_window(train, 500)
X_test, y_test = make_observation_window(test, 500)

scaler = StandardScaler()
for i in range(X_train.shape[0]):
    X_train[i] = scaler.fit_transform(X_train[i].values)

for i in range(X_test.shape[0]):
    X_test[i] = scaler.fit_transform(X_test[i].values)

train_generator = CustomDataGenerator(X_train.values, y_train, 128)
test_generator = CustomDataGenerator(X_test.values, y_test, 128)

In [ ]:
print(X_train.shape)
print(y_train.shape)

In [ ]:

early_stopping = EarlyStopping(monitor='val_auc',  # метрика для мониторинга
                               patience=6,  # количество эпох, в течение которых можно пропустить улучшение
                               verbose=1,  # выводит сообщение, когда обучение останавливается
                               restore_best_weights=True)  # восстанавливает лучшие веса, найденные во время обучения
model = Sequential([
    layers.InputLayer(input_shape=(X_train.shape[1], X_train.shape[2])),
    layers.Conv1D(filters=8, kernel_size=40, activation='relu', padding='same'),
    layers.MaxPooling1D(pool_size=2, padding='same'),
    layers.Conv1D(filters=16, kernel_size=20, activation='relu', padding='same'),
    layers.MaxPooling1D(pool_size=2, padding='same'),
    # layers.Conv1D(filters=128, kernel_size=25, activation='relu', padding='same'),
    # layers.MaxPooling1D(pool_size=2, padding='same'),
    # layers.Conv1D(filters=256, kernel_size=12, activation='relu', padding='same'),
    # layers.MaxPooling1D(pool_size=2, padding='same'),
    # layers.Conv1D(filters=512, kernel_size=6, activation='relu', padding='same'),
    # layers.MaxPooling1D(pool_size=2, padding='same'),
    # layers.Conv1D(filters=1024, kernel_size=3, activation='relu', padding='same'),
    # layers.MaxPooling1D(pool_size=2, padding='same'),
    # layers.Conv1D(filters=64, kernel_size=10, activation='relu', padding='same'),
    # layers.MaxPooling1D(pool_size=2, padding='same'),
    # layers.Conv1D(filters=128, kernel_size=8, activation='tanh', padding='same'),
    # layers.MaxPooling1D(pool_size=2, padding='same'),
    # layers.LSTM(64, activation='tanh', return_sequences=True),
    layers.LSTM(64, activation='tanh'),
    layers.Flatten(),
    layers.Dense(64, activation='relu'),
    layers.Dropout(0.2),
    layers.Dense(64, activation='relu'),
    layers.Dropout(0.2),
    layers.Dense(1, activation='sigmoid')
])

# Компиляция модели
model.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=[tf.keras.metrics.AUC(name='auc')],
              )

# Обучение модели
class_weights = {0: 1, 1: 2.256}  # 2.25:1
history = model.fit(
    train_generator,
    epochs=100,
    # batch_size=100,
    validation_data=test_generator,
    verbose=1,
    callbacks=[early_stopping],
    class_weight=class_weights,
)

# Оценка модели с использованием другой метрики
model.compile(metrics=[tf.keras.metrics.AUC(name='auc'), f1_metric])
loss, test_auc, test_f1 = model.evaluate(test_generator)
print(f"Test AUC: {test_auc:.5f}, test_f1: {test_f1:.5f}")

In [ ]:
_, val_klines = split_data(klines, .8)
indicators_w = [*indicators, {'prob_col': 'buy'}]
env_kwargs = dict(
    env_class='TradingEnv1BoxAction',
    tester='BBTester',
    # tester='BBFreeActionTester',
    klines=val_klines.iloc[:-300],
    data=None,
    indicators=indicators_w,
    verbose=1,
    # b_size=1000,
)
env = make_env(**env_kwargs)

In [ ]:
done = False
obs = env.reset()
while not done:
    tick = env.envs[0].tester.tick
    n_tick = env.envs[0].tester.n_tick
    action = [[0.5]]

    if tick['close'] <= tick['bb_lower']:
        try:
            obs = X_test.sel(time=tick['open_time']).values
            action = model.predict(obs[None, :, :], verbose=0)
        except KeyError:
            pass
    
    obs, reward, done, info = env.step(action)
    # env.render()

In [ ]:
done = False
obs = env.reset()
while not done:
    action = [[1]]
    obs, reward, done, info = env.step(action)
    env.render()